In [76]:
import pandas as pd
import ast
import numpy as np
from tqdm import tqdm


In [3]:
import torch
import torch.nn as nn
from collections import Counter
import ast
from torch.utils.data import Dataset, DataLoader
import torch
from torch.utils.data import DataLoader, TensorDataset

In [4]:
device = torch.device('mps')

# 데이터 정제

In [5]:
df1 = pd.read_csv('./data/userList (10001~20001).csv')
df2 = pd.read_csv('./data/userList(20001~30000).csv')
df3 = pd.read_csv('./data/userList(30000~40001).csv')
df4 = pd.read_csv('./data/userList(40001~50001).csv')
df5 = pd.read_csv('./data/userList.csv')


In [6]:
# DataFrame들을 리스트로 결합
#dfs = [df1, df2, df3, df4, df5]
dfs = [df1, df2, df3, df4]

# concat 함수를 사용하여 DataFrame들을 하나로 합침
combined_df = pd.concat(dfs)



In [7]:
combined_df.reset_index(drop=True, inplace=True)

In [9]:
df5.columns = combined_df.columns

In [11]:
df5.dropna(inplace=True)

In [12]:
combined_df = pd.concat([combined_df, df5])

In [13]:
combined_df.reset_index(drop=True, inplace=True)

In [14]:
col = 'rank	rightCnt	wrongCnt	time out	memory exceed	print exceed	runTime error	compile error	solvedProblemList	triedNotsolvedList'
col = col.split('\t')

In [15]:
def check_no_list(c, df):
    temp = df[df[c] == '[]']
    return temp

In [16]:
is_null = pd.DataFrame()

In [17]:
for i in range(len(col)):
    temp = check_no_list(col[i], combined_df)
    is_null = pd.concat([temp, is_null])

In [19]:
# is_null 데이터프레임에 있는 행의 인덱스를 가져옴
drop_indices = is_null.index

# 이 인덱스를 사용하여 combined_df에서 해당 행을 제거
combined_df_dropped = combined_df.drop(drop_indices)


In [20]:
df = combined_df_dropped.reset_index(drop=True)

In [24]:
tier_0 = df[df['tier'] == 0].index
df.drop(tier_0, inplace=True)

In [25]:
# 문자열을 리스트로 변환하는 함수 정의
def string_to_list(s):
    try:
        return ast.literal_eval(s)
    except ValueError:
        return []  # 또는 적절한 기본값 반환

In [26]:
# 리스트로 꺼내도 될 칼럼 정의
li='rank	rightCnt	wrongCnt	time out	memory exceed	print exceed	runTime error	compile error'
col = li.split('\t')

# 리스트 안 숫자 꺼내는 함수
def turn_num(s):
    cs = s.apply(string_to_list).explode()
    return cs

# 데이터프레임에 모두 적용
for i in range(len(col)):
    df[col[i]] = turn_num(df[col[i]])
for column in col:
    df[column] = pd.to_numeric(df[column], errors='coerce')

    invalid_rows = df[df[column].isnull()]

In [30]:
df[col] = df[col].apply(lambda x: x.fillna(0).astype(int))

In [31]:
df.reset_index(drop=True, inplace=True)

In [33]:
# 숫자형 변환
df['tier'] = df['tier'].astype(int)

In [37]:
# 데이터 처리를 위한 코드 (이미 제공됨)
df['solvedProblemList'] = df['solvedProblemList'].apply(ast.literal_eval)
df['triedNotsolvedList'] = df['triedNotsolvedList'].apply(ast.literal_eval)

In [38]:
# 문제 번호의 빈도를 계산하기 위한 Counter 객체 초기화
problem_counts = Counter()

In [39]:
# solvedProblemList 칼럼에서 문제 번호의 빈도를 계산
for problem_list in df['solvedProblemList']:
    problem_counts.update(problem_list)

In [40]:
# triedNotsolvedList 칼럼에서 문제 번호의 빈도를 계산
for problem_list in df['triedNotsolvedList']:
    problem_counts.update(problem_list)


In [42]:
len(problem_counts)

24341

In [43]:
# problem_counts에서 값이 5000 이상인 항목만 필터링
filtered_problems = {problem: count for problem, count in problem_counts.items() if count >= 5000}


In [44]:
len(filtered_problems)

691

In [45]:
# 필터링된 문제 번호 집합 생성
filtered_problems_set = set(filtered_problems.keys())

# solvedProblemList와 triedNotsolvedList에서 필터링된 문제 번호만 유지
df['solvedProblemList'] = df['solvedProblemList'].apply(lambda x: [problem for problem in x if problem in filtered_problems_set])
df['triedNotsolvedList'] = df['triedNotsolvedList'].apply(lambda x: [problem for problem in x if problem in filtered_problems_set])


# EASE 모델

## 모델에 들어가기 위한 데이터 변환

In [46]:
# 모든 문제의 고유 목록 생성
all_problems = set()
for row in df.itertuples():
    all_problems.update(row.solvedProblemList)
    all_problems.update(row.triedNotsolvedList)
all_problems = sorted(all_problems)

In [48]:
# 이진 상호작용 행렬 생성
interaction_matrix = pd.DataFrame(0, index=df['id'], columns=all_problems)


In [49]:
for row in df.itertuples():
    interaction_matrix.loc[row.id, row.solvedProblemList] = 1

In [50]:
# 검증 데이터셋과 훈련데이터셋 나누기

# 검증 데이터에 사용할 문제 수
num_valid_per_user = 10

# 검증 데이터 선택
valid_indices = {}

for user_id in interaction_matrix.index:
    # 사용자가 푼 문제 인덱스
    solved_problems = interaction_matrix.columns[interaction_matrix.loc[user_id] == 1]

    # 사용자가 푼 문제의 수가 num_valid_per_user보다 크거나 같은 경우에만 처리
    if len(solved_problems) >= num_valid_per_user:
        # 중복 없이 무작위 추출
        valid_problems = np.random.choice(solved_problems, num_valid_per_user, replace=False)
        valid_indices[user_id] = valid_problems
    else:
        # 사용자가 푼 문제의 수가 부족한 경우, 이 사용자에 대한 처리를 건너뜀
        # 필요에 따라 여기서 다른 처리를 할 수도 있음
        continue


# 검증 데이터를 저장할 딕셔너리
valid_dict = {user_id: interaction_matrix.columns.get_indexer(valid_indices[user_id]) for user_id in valid_indices}


In [51]:
# 훈련 데이터를 위한 복사본 생성
train_matrix = interaction_matrix.copy()

# 검증 데이터를 훈련 데이터에서 제거
for user_id, valid_problems in valid_indices.items():
    train_matrix.loc[user_id, valid_problems] = 0


In [52]:
interaction_matrix

1000  1001  1002  10026  1003  10039  1004  1005  1008  1009  ...  \
id                                                                        ...   
jh5154         1     1     0      0     1      1     0     0     1     0  ...   
baefr          1     1     1      1     0      0     0     0     1     0  ...   
nacean         1     1     0      1     1      1     0     0     1     1  ...   
klxex          0     0     0      1     1      1     0     1     0     0  ...   
qortndud97     1     1     0      0     0      1     0     1     1     1  ...   
...          ...   ...   ...    ...   ...    ...   ...   ...   ...   ...  ...   
kjsmel         1     1     0      0     0      0     0     0     1     0  ...   
limy0213       1     1     0      0     0      1     0     0     1     0  ...   
palzmnbvcx     1     1     0      0     0      0     0     0     1     0  ...   
planet4869     1     1     0      0     0      0     0     0     0     0  ...   
q7011805       1     1     0      0     0      0     0     0     1     0  ...   

            9506  9610  9613  9625  9653  9654  9655  9656  9663  9935  
id                                                                      
jh5154         1     0     1     0     0     0     0     0     1     1  
baefr          0     0     0     0     0     0     0     0     1     0  
nacean         0     0     0     1     0     1     0     0     1     0  
klxex          0     0     0     0     0     0     0     0     1     1  
qortndud97     1     0     0     1     0     0     0     0     1     0  
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
kjsmel         0     0     0     0     0     0     0     0     0     0  
limy0213       0     0     0     0     0     0     0     0     0     0  
palzmnbvcx     0     0     0     0     0     0     0     0     0     0  
planet4869     0     0     0     0     0     0     0     0     0     0  
q7011805       0     0     0     0     0     0     0     0     0     0  

[84022 rows x 691 columns]

In [53]:
# 각 사용자별 검증 데이터의 길이 확인
for user_id in valid_dict:
    print(f"User {user_id} has {len(valid_dict[user_id])} validation problems.")


User jh5154 has 10 validation problems.
User baefr has 10 validation problems.
User nacean has 10 validation problems.
User klxex has 10 validation problems.
User qortndud97 has 10 validation problems.
User kgs9321 has 10 validation problems.
User me081004 has 10 validation problems.
User plerin152 has 10 validation problems.
User jungri823 has 10 validation problems.
User iphuck22 has 10 validation problems.
User jsb12302 has 10 validation problems.
User junghoyoon505 has 10 validation problems.
User youmean0427 has 10 validation problems.
User test3014 has 10 validation problems.
User sj155 has 10 validation problems.
User spire99 has 10 validation problems.
User qkrwlgns7 has 10 validation problems.
User guseoh has 10 validation problems.
User zlfn94 has 10 validation problems.
User seewoo5 has 10 validation problems.
User ddilgu has 10 validation problems.
User kywoo26 has 10 validation problems.
User seungmin_py has 10 validation problems.
User wmwmw98213 has 10 validation problem

In [54]:
# 데이터프레임을 PyTorch 텐서로 변환
train_tensor = torch.tensor(train_matrix.values).float().to(device)

## 모델 설계

In [58]:
import gc

gc.collect()
torch.mps.empty_cache()

In [59]:
def get_hit(pred_list, true_list):
    hit_list = set(true_list) & set(pred_list)
    hit = len(hit_list) / len(true_list)
    return hit

In [79]:
class EASE(nn.Module):
    def __init__(self, num_items, reg_lambda=500):
        super(EASE, self).__init__()
        self.reg_lambda = reg_lambda
        self.num_items = num_items
        self.item_weights = nn.Parameter(torch.zeros(num_items, num_items))
        self.device = torch.device('mps')

    def forward(self, x):
        # x: 사용자-아이템 상호작용 행렬
        return torch.matmul(x, self.item_weights)
    def clear_memory(self):
        gc.collect()
        torch.cuda.empty_cache()
    
    def fit(self, data_loader):
        self.item_weights.data.zero_()  # 가중치 초기화

        for batch in data_loader:
            # 데이터 텐서 추출
            data_tensor = batch[0].to(self.device)

            # 배치에 대한 Gram Matrix 계산
            G_batch = torch.matmul(data_tensor.T, data_tensor) + self.reg_lambda * torch.eye(self.num_items, device=self.device)

            # Batch Gram Matrix의 역행렬 계산
            P_batch = torch.inverse(G_batch)

            # Batch Item Weights 계산
            B_batch = P_batch / -torch.diag(P_batch)
            B_batch.fill_diagonal_(0)

            # 각 배치의 결과를 누적
            self.item_weights.data += B_batch

        # 평균 가중치 계산
        self.item_weights.data /= len(data_loader)



In [61]:


# 사용자 정의 데이터셋 클래스
class CustomDataset(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        return self.data[idx]


In [62]:

# TensorDataset 및 DataLoader 생성
dataset = TensorDataset(train_tensor)
data_loader = DataLoader(dataset, batch_size=3000, shuffle=True)  # 배치 크기는 조절 가능


## 모델 학습

In [69]:
# 모델 초기화
# 문제 2000이하, 배치 오천으로 했더니 셧다운
# 문제 5000이하, 배치 3천 가능
model = EASE(num_items=train_tensor.shape[1], reg_lambda=1000).to(device)
# 람다 500 
# 모델 훈련
model.fit(data_loader)


In [77]:
batch_size = 3000

In [70]:
# 검증 데이터셋에 대한 모델 예측 수행
valid_tensor = torch.tensor(train_matrix.values).float().to(device)
predictions = model(valid_tensor)


## 모델 테스트

In [72]:
user_name_to_idx = {name: idx for idx, name in enumerate(interaction_matrix.index)}
valid_dict_indexed = {user_name_to_idx[user_id]: valid_problems for user_id, valid_problems in valid_dict.items()}


In [73]:
# 성능 평가를 위한 함수 정의
def get_hit_rate(predictions, valid_dict):
    hit = 0
    total = 0

    for user_id, valid_problems in valid_dict.items():
        # 모델이 예측한 점수에서 검증 문제에 해당하는 점수 추출
        user_pred_scores = predictions[user_id, valid_problems]

        # 사용자가 실제로 풀었던 문제의 점수가 높은지 확인
        # 예시: 상위 N개 중에 실제 풀었던 문제가 몇 개인지 세기
        hit += (user_pred_scores > 0.5).sum().item()
        total += len(valid_problems)

    # 평균 히트율 계산
    return hit / total if total > 0 else 0


In [74]:
# 성능 평가
hit_rate = get_hit_rate(predictions, valid_dict_indexed)
print(f"Hit Rate: {hit_rate:.4f}")
# 람다 500 -> 0.52 어쩌구 아닌가 잘 모름
# 람다 1000 -> 0.5501

Hit Rate: 0.5501


## 모델 튜닝

In [80]:
for reg in tqdm([100000, 50000, 10000, 5000, 1000, 100, 1]):
    data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True)  # 배치 크기는 조절 가능
    model = EASE(num_items=train_tensor.shape[1], reg_lambda=reg).to(device)
    model.fit(data_loader)
    model.clear_memory()


    valid_tensor = torch.tensor(train_matrix.values).float().to(device)
    predictions = model(valid_tensor)

    hit_rate = get_hit_rate(predictions, valid_dict_indexed)
    print(f"Hit Rate: {hit_rate:.4f}")


 14%|█▍        | 1/7 [01:15<07:33, 75.57s/it]

Hit Rate: 0.0576


 29%|██▊       | 2/7 [02:31<06:19, 75.83s/it]

Hit Rate: 0.1431


 43%|████▎     | 3/7 [03:43<04:57, 74.26s/it]

...

Hit Rate: 0.5504


 86%|████████▌ | 6/7 [07:28<01:15, 75.06s/it]

Hit Rate: 0.6376


100%|██████████| 7/7 [08:45<00:00, 75.14s/it]

Hit Rate: 0.6625


In [81]:

# 시도할 규제 파라미터와 배치 사이즈 목록
reg_values = [5000, 1000, 500, 300, 100, 10, 1]
batch_sizes = [1000, 3000, 5000, 7000]  

for reg in tqdm(reg_values):
    for batch_size in batch_sizes:
        # 데이터 로더 생성
        data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

        # 모델 초기화 및 훈련
        model = EASE(num_items=train_tensor.shape[1], reg_lambda=reg).to(device)
        model.fit(data_loader)

        # 모델 메모리 정리 (해당 메소드가 필요하다면)
        if hasattr(model, 'clear_memory'):
            model.clear_memory()

        # 검증 데이터셋에 대한 예측
        valid_tensor = torch.tensor(train_matrix.values).float().to(device)
        predictions = model(valid_tensor)

        # 히트율 계산 및 출력
        hit_rate = get_hit_rate(predictions, valid_dict_indexed)
        print(f"Reg: {reg}, Batch Size: {batch_size}, Hit Rate: {hit_rate:.4f}")


  0%|          | 0/7 [00:00<?, ?it/s]

Reg: 5000, Batch Size: 1000, Hit Rate: 0.3345
Reg: 5000, Batch Size: 3000, Hit Rate: 0.4279
Reg: 5000, Batch Size: 5000, Hit Rate: 0.4857


 14%|█▍        | 1/7 [04:53<29:19, 293.31s/it]

Reg: 5000, Batch Size: 7000, Hit Rate: 0.4722
Reg: 1000, Batch Size: 1000, Hit Rate: 0.4786
Reg: 1000, Batch Size: 3000, Hit Rate: 0.5504
Reg: 1000, Batch Size: 5000, Hit Rate: 0.5903


 29%|██▊       | 2/7 [09:56<24:55, 299.00s/it]

...

Reg: 100, Batch Size: 7000, Hit Rate: 0.6416
Reg: 10, Batch Size: 1000, Hit Rate: 0.6529
Reg: 10, Batch Size: 3000, Hit Rate: 0.6597
Reg: 10, Batch Size: 5000, Hit Rate: 0.6668


 86%|████████▌ | 6/7 [30:32<05:07, 307.48s/it]

Reg: 10, Batch Size: 7000, Hit Rate: 0.6548
Reg: 1, Batch Size: 1000, Hit Rate: 0.6647
Reg: 1, Batch Size: 3000, Hit Rate: 0.6629
Reg: 1, Batch Size: 5000, Hit Rate: 0.6684


100%|██████████| 7/7 [35:35<00:00, 305.08s/it]

Reg: 1, Batch Size: 7000, Hit Rate: 0.6559
